### Script pour le controle des données brutes issues de la chaine INSIGHT
### Etude de conformité des fichiers

In [20]:
import logging
from filecmp import dircmp
from os import listdir
import os
import filecmp
from dotenv import load_dotenv
from intake import open_catalog
import matplotlib as plt
import pandas as pd
import numpy as np
from shapely import wkt
import shapely
from sqlalchemy import create_engine
from shapely.geometry import shape
from shapely.ops import unary_union
from geopandas import GeoDataFrame
import geopandas as gpd
from datetime import datetime
import networkx as nx
from shapely.geometry import MultiPolygon

load_dotenv()

## Create log file 
logging.basicConfig(filename='N:/Informatique/SIG/Etudes/2023/2309_QC_feux/Travail/Scripts/Controle_data/log_Controle_data_brute.log',filemode='w', encoding='utf-8', level=logging.INFO, force=True, format='%(message)s')

##open yaml file to get raw buned area table
catfeux = open_catalog(f'{os.getenv("PROJECT_PATH")}/Fire_Detection_Data_Quality.yaml')

toto = catfeux.Surfaces_brulees_brute_control.read()

date_start=pd.to_datetime("2023-01-01", format="%Y-%m-%d")
date_end=pd.to_datetime("2023-12-31", format="%Y-%m-%d")

#date_start=datetime.strptime("2023-01-01","%Y-%m-%d") 
#date_end=datetime.strptime("2023-10-31","%Y-%m-%d")

## Début des contrôles

In [3]:
def get_all_elements_in_list_of_lists(list):
    count = 0
    for element in list:
        count += len(element)
    return count

### Check if tile's name are differents than the 15 use in NC

In [4]:

logging.info('------------------------------------------------')
logging.info('Check if unknown tiles are found in data')
logging.info('------------------------------------------------')

## liste des 15 tuiles présentes sur la GT et les iles 
list_tiles=['L2A_T58KCC','L2A_T58KCD','L2A_T58KDB','L2A_T58KDC','L2A_T58KEA','L2A_T58KEB','L2A_T58KEC',
            'L2A_T58KFA','L2A_T58KFB','L2A_T58KFC','L2A_T58KGA','L2A_T58KGB','L2A_T58KGC','L2A_T58KGV','L2A_T58KHB']

## prendre que le numéro de la dalle pour les traitements
surfdetect_control['nom'] = [x[-10:] for x in surfdetect_control['nom']]

error_tile=[]

for i in range(len(surfdetect_control)):
    if surfdetect_control['nom'][i] in list_tiles:
         continue
    else:
        error_tile.append(surfdetect_control.iloc[i]) ## on regarde si d'autres tuiles sont présentes dans le jeu de donnée

if not error_tile:
    print('Aucune tuiles détectées en dehors des 15 tuiles utilisées par l algorithme')
    logging.info('Not unkonw tiles found in data - continue process')
    len_error_tile=0
else:
    error_tile=pd.concat(error_tile,axis=1, ignore_index=True).T
    print('Attention des tuiles en dehors des tuiles abituelles sont présentes dans le jeux de donnée')
    logging.error('%s !! WARNING !! Unknow tile found in data - check ogc_fid number above or in code !! :', error_tile['ogc_fid']) ## on alimente le log si présence de tuiles autres
    len_error_tile=len(error_tile)

logging.info('Number of tiles detected outside the 15 tiles', len_error_tile)

Aucune tuiles détectées en dehors des 15 tuiles utilisées par l algorithme


--- Logging error ---
Traceback (most recent call last):
  File "c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\logging\__init__.py", line 1110, in emit
    msg = self.format(record)
          ^^^^^^^^^^^^^^^^^^^
  File "c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\logging\__init__.py", line 953, in format
    return fmt.format(record)
           ^^^^^^^^^^^^^^^^^^
  File "c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\logging\__init__.py", line 687, in format
    record.message = record.getMessage()
                     ^^^^^^^^^^^^^^^^^^^
  File "c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\logging\__init__.py", line 377, in getMessage
    msg = msg % self.args
          ~~~~^~~~~~~~~~~
TypeError: not all arguments converted during string formatting
Call stack:
  File "<frozen runpy>", line 198, in _run_module_as_main
  File "<frozen runpy>", line 88, in _run_code
  File "c:\Users\oriane.bruyere\AppData\Local

### Check if tile occurence is equal to zero

In [5]:
### Check if tile occurence is equal to zero
## traitement à prendre avec des pincettes car selon la résolution temporelle des données des tuiles peuvent manquer 

logging.info('------------------------------------------------')
logging.info('Check if tile occurence is set to 0')
logging.info('------------------------------------------------')

df_dalle=pd.DataFrame({"date":surfdetect_control.date,"dalle_names":surfdetect_control.nom})
## prendre que le numéro de la dalle
df_dalle['dalle_names'] = [x[-10:] for x in df_dalle['dalle_names']]
df_dalle=df_dalle.set_index(df_dalle['date'])
df_dalle = df_dalle.sort_index()

occurrences_dalles = df_dalle["dalle_names"].value_counts()
print(occurrences_dalles)

values_at_zero = occurrences_dalles[occurrences_dalles == 0].index

if not values_at_zero.empty:
    logging.error('%s !! WARNING !! Tile occurence is set to 0 - check tile name above or in code !! :', values_at_zero)
    print(values_at_zero)
else:
    logging.info('Tile occurence is different than 0 in data - continue process')

dalle_names
L2A_T58KEB    8180
L2A_T58KDC    7496
L2A_T58KDB    4523
L2A_T58KFA    2366
L2A_T58KFB    2196
L2A_T58KEA    1845
L2A_T58KCC     708
L2A_T58KEC     622
L2A_T58KCD     595
L2A_T58KGB     365
L2A_T58KHB     171
L2A_T58KGA      79
L2A_T58KGV      45
L2A_T58KGC      23
L2A_T58KFC      17
Name: count, dtype: int64


### Check if burned area are under 1ha

In [6]:
## Check if burned area are under 1ha

logging.info('------------------------------------------------')
logging.info('Check if burned areas are not under 1 ha')
logging.info('------------------------------------------------')

error_surface=[]

for i in range(len(surfdetect_control)):
    if surfdetect_control['surface'][i] >= 1:
         continue
    else:
        error_surface.append(surfdetect_control.iloc[i])

if not error_surface:
    print('empty_list')
    logging.info('No surface found under 1ha - continue process')
    len_error_surface=0
else:
    error_surface=pd.concat(error_surface,axis=1, ignore_index=True).T
    print('list if not empty')
    logging.error('%s !! WARNING !! burned areas are found under 1 ha - check ogc_fid number above or in code !! :', error_surface['ogc_fid'])
    len_error_surface=len(error_surface)

logging.info('Number polygons under 1ha ', len_error_surface)

empty_list


--- Logging error ---
Traceback (most recent call last):
  File "c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\logging\__init__.py", line 1110, in emit
    msg = self.format(record)
          ^^^^^^^^^^^^^^^^^^^
  File "c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\logging\__init__.py", line 953, in format
    return fmt.format(record)
           ^^^^^^^^^^^^^^^^^^
  File "c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\logging\__init__.py", line 687, in format
    record.message = record.getMessage()
                     ^^^^^^^^^^^^^^^^^^^
  File "c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\logging\__init__.py", line 377, in getMessage
    msg = msg % self.args
          ~~~~^~~~~~~~~~~
TypeError: not all arguments converted during string formatting
Call stack:
  File "<frozen runpy>", line 198, in _run_module_as_main
  File "<frozen runpy>", line 88, in _run_code
  File "c:\Users\oriane.bruyere\AppData\Local

### Check if geometries have errors

In [ ]:
## Check if burned area have wrong geometries

logging.info('------------------------------------------------')
logging.info('Check if burned areas have wrong geometries')
logging.info('------------------------------------------------')

is_valid = surfdetect_control.geometry.is_valid
invalid_geometries = surfdetect_control[~is_valid]
len_invalid_geometries=len(invalid_geometries)

print("Multipolygones with geometries errors :",invalid_geometries)
logging.error('%s !! WARNING !! burned areas geometries have errors - check ogc_fid number above or in code !! :', invalid_geometries.index)

surfdetect_control.geometry = surfdetect_control.geometry.buffer(0) # correct the geometry

## check if the correction is applied
is_valid_after_correction = surfdetect_control.geometry.is_valid
invalid_geometries_after_correction = surfdetect_control[~is_valid_after_correction]
print("Check if geometry correction were applied :", invalid_geometries_after_correction)
logging.error('%s !! WARNING !! a geometry correction were applied - if empty continue process : ',invalid_geometries_after_correction)

#### Check if burned areas are detected outside date interval set at the begening

In [7]:
## Check if burned areas are detected outside date interval set at the begening

logging.info('------------------------------------------------')
logging.info('%s Check if burned areas are included into the following date interval', )
logging.info('------------------------------------------------')

error_date=[]

for i in range(len(surfdetect_control)):
    current_date = pd.to_datetime(surfdetect_control['date'][i])
    
    if date_start <= current_date <= date_end:
        continue
    else:
        error_date.append(surfdetect_control.iloc[i])

if not error_date:
    print('empty_list')
    logging.info('Burned areas are included into date range - continue process')
    len_outside_date=0
else:
    error_date=pd.concat(error_date,axis=1, ignore_index=True).T
    print('list if not empty')
    logging.error('%s !! WARNING !! burned areas are found outside date range - check ogc_fid number above or in code !! :', error_date['ogc_fid'])
    len_outside_date=len(error_date)

logging.info('Number polygons outiside the date range ', len_outside_date)

empty_list


--- Logging error ---
Traceback (most recent call last):
  File "c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\logging\__init__.py", line 1110, in emit
    msg = self.format(record)
          ^^^^^^^^^^^^^^^^^^^
  File "c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\logging\__init__.py", line 953, in format
    return fmt.format(record)
           ^^^^^^^^^^^^^^^^^^
  File "c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\logging\__init__.py", line 687, in format
    record.message = record.getMessage()
                     ^^^^^^^^^^^^^^^^^^^
  File "c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\logging\__init__.py", line 377, in getMessage
    msg = msg % self.args
          ~~~~^~~~~~~~~~~
TypeError: not all arguments converted during string formatting
Call stack:
  File "<frozen runpy>", line 198, in _run_module_as_main
  File "<frozen runpy>", line 88, in _run_code
  File "c:\Users\oriane.bruyere\AppData\Local

In [8]:
## create an id
surfdetect_control['ID'] = range(1, len(surfdetect_control)+1,1)

### Check if identical geometries are observed at a same date

In [9]:
#check if identical geometries are observed at a same date
len_surfdetect_control_before=len(surfdetect_control)
def compare_geometries(gdf):
    geometry_date_dict = {}

    for index, row in gdf.iterrows():
        geometry =  row['geometry']
        date = row['date']

        # Convertir la géométrie en une forme Shapely
        geom_shape = shape(geometry)
        key = (geom_shape, date)

        # Ajouter la paire (forme, date) au dictionnaire
        if key not in geometry_date_dict:
            geometry_date_dict[key] = []

        geometry_date_dict[key].append(index)
    identique_geom=[]
    
    # identifier les géométries avec la même forme à la même date = doublon
    for key, indices in geometry_date_dict.items():
        if len(indices) > 1:
            identique_geom.append(indices)
            print(f"Géométries identiques à la même date : {indices}")
    
    return(identique_geom)

surfdetect_control['geometry']=shapely.wkt.loads(shapely.wkt.dumps(surfdetect_control['geometry'], rounding_precision=1)) ## change number of decimal for geometry
identique_geom=compare_geometries(surfdetect_control) 

logging.info('------------------------------------------------')
logging.info('%s Check if 2 identical geometries shape are observed at a same date', )
logging.info('------------------------------------------------')

if not identique_geom:
    print('empty_list')
    logging.info('NO identical geometries found at the same date - continue process')
    len_identique_geom=0
else:
    print('list if not empty')
    len_identique_geom=len(identique_geom)
    #logging.error('%s !! WARNING !! same geometries at a same date were found - check ogc_fid number above or in code !! :', identique_geom.index)
    
    ### if identical geometries are found : check if they have the name tile name
    for sublist in identique_geom:
        nom_values = [surfdetect_control.loc[i, 'nom'] for i in sublist]
        index_values=[surfdetect_control.loc[i, 'ID'] for i in sublist]
        if all(value == nom_values[0] for value in nom_values):
            print('nom de thuile identique')
            logging.error('%s !! WARNING !! same geometries at a same date were found on a same tile: check above for informations',index_values)
            
            ## we keep the first geom et delete the others
            if len(sublist) == 2: 
                surfdetect_control=surfdetect_control.drop(sublist[1])
                print('delete index : ',sublist[1])
            else:
                surfdetect_control=surfdetect_control.drop(sublist[1:])
                print('delete index :',sublist[1:])
        else:
            print('nom de thuile différente')
            logging.error('%s !! WARNING !! same geometries at a same date were found on different tiles : check above for informations',index_values)
            
            ## we keep the first geom et delete the others
            if len(sublist) == 2: 
                surfdetect_control=surfdetect_control.drop(sublist[1])
                print('delete index : ',sublist[1])
            else:
                surfdetect_control=surfdetect_control.drop(sublist[1:])
                print('delete index :',sublist[1:])

surfdetect_control=surfdetect_control.reset_index(drop=True)
surfdetect_control['ID'] = range(1, len(surfdetect_control)+1,1)

Géométries identiques à la même date : [2280, 2387]
Géométries identiques à la même date : [2281, 2386]
Géométries identiques à la même date : [2282, 2385]
Géométries identiques à la même date : [2283, 2355]
Géométries identiques à la même date : [2284, 2384]
Géométries identiques à la même date : [2285, 2383]
Géométries identiques à la même date : [2286, 2382]
Géométries identiques à la même date : [2287, 2379]
Géométries identiques à la même date : [2288, 2374]
Géométries identiques à la même date : [2289, 2375]
Géométries identiques à la même date : [2290, 2376]
Géométries identiques à la même date : [2291, 2381]
Géométries identiques à la même date : [2292, 2377]
Géométries identiques à la même date : [2293, 2388]
Géométries identiques à la même date : [2294, 2378]
Géométries identiques à la même date : [2295, 2380]
Géométries identiques à la même date : [2296, 2373]
Géométries identiques à la même date : [2297, 2391]
Géométries identiques à la même date : [2298, 2371]
Géométries i

## Overlapping polygons for a same date

### Create intersected group of polygons at a same date

In [11]:
def find_intersecting_id(row, gdf):
    # Filtrer le GeoDataFrame pour les polygones à la même date
    gdf_same_date = gdf[gdf['date'] == row['date']]
    
    # Utiliser `sindex` pour une recherche spatiale plus efficace parmi ceux de la même date
    possible_matches_index = list(gdf_same_date.sindex.intersection(row['geometry'].bounds))
    possible_matches = gdf_same_date.iloc[possible_matches_index]
    precise_matches = possible_matches[possible_matches.geometry.intersects(row['geometry'])]
    
    intersecting_ids = precise_matches['ID'].tolist()
    intersecting_ids = [id_ for id_ in intersecting_ids if id_ != row['ID']]
    
    return intersecting_ids

G = nx.Graph()
for index, row in surfdetect_control.iterrows():
    intersecting_ids = find_intersecting_id(row, surfdetect_control)
    for id_ in intersecting_ids:
        G.add_edge(row['ID'], id_)

groupes = list(nx.connected_components(G))
for groupe_id, groupe in enumerate(groupes):
    for id_ in groupe:
        surfdetect_control.loc[surfdetect_control['ID'] == id_, 'groupe_id'] = groupe_id

### Check if overlapping geometries are around tile's limit

In [12]:
tile_stl2 = catfeux.tile_sentinel2_line_UTM.read() ## ouvirr la table des limites des tuiles Sentinel2
tile_stl2=tile_stl2.set_index(tile_stl2['Name']) ## mettre en index le nom de la tuile

group_ids = surfdetect_control['groupe_id'].unique()
delete_index_tiles_limits=[]

logging.info('------------------------------------------------')
logging.info('%s Check if overlapping geometries at a same date are observed close to tile limits ', )
logging.info('------------------------------------------------')

for group_id in group_ids:
    # Sélectionnez les données pour le groupe en cours
    group_data = surfdetect_control[surfdetect_control['groupe_id'] == group_id]
    group_data['nom']= [x[-5:] for x in group_data['nom']]
    if group_data.shape[0] >= 2 :

        for i in range(len(group_data)):
            if group_data.iloc[i]['geometry'].buffer(20).intersects(tile_stl2['geometry'].loc[group_data.iloc[i]['nom']]):
                print("tile touche",group_data.iloc[i]["ID"]-1)
                surfdetect_control.drop(group_data.iloc[i]["ID"]-1,inplace=True)
                logging.error('%s !! WARNING !! Intersection between geometry and tile limits were found : check above for informations',group_data.iloc[i]["ID"]-1)
                delete_index_tiles_limits.append(group_data.iloc[i]["ID"]-1)

c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning:

tile touche 447
tile touche 495
tile touche 762
tile touche 760
tile touche 761
tile touche 1005


c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning:

tile touche 1233
tile touche 1372
tile touche 1412
tile touche 1664


c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning:

...

c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning:

tile touche 22185
tile touche 22190
tile touche 22592
tile touche 22591


c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning:

tile touche 22640
tile touche 22609


c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning:

### Check if overlapping geometries are from differents tiles

In [16]:
group_ids = surfdetect_control['groupe_id'].unique()
delete_index_same_tiles_geom=[]

logging.info('------------------------------------------------')
logging.info('%s Check if overlapping geometries at a same date are observed from a same tile ', )
logging.info('------------------------------------------------')

for group_id in group_ids:
    
    group_data = surfdetect_control[surfdetect_control['groupe_id'] == group_id]
    group_data['nom']= [x[-5:] for x in group_data['nom']]
    if group_data.shape[0] >= 2 :
        if all(v == group_data['nom'].iloc[0] for v in group_data['nom']):
            print(f"les noms des tuiles sont identiques.", group_data)
            logging.error('%s !! WARNING !! overlapping geometries at a same date were found on a same tile : check above for informations',group_data)
        
        else: ## we merge geometries overlapping from differents tiles
            print(f"les noms des tuiles sont différents")
            nouveau_polygone = unary_union(group_data['geometry'])
            surfdetect_control.at[group_data.iloc[0]["ID"]-1,'geometry'] = nouveau_polygone
            surfdetect_control.drop(group_data.iloc[1:]["ID"]-1,inplace=True)
            delete_index_same_tiles_geom.append(group_data.iloc[i]["ID"]-1)


c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning:

les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont identiques.         date    nom       province    commune    surface       x       y  \
52  20230103  58KDB  Province Nord  POUEMBOUT   2.341498  295531  344719   
55  20230103  58KDB  Province Nord  POUEMBOUT   7.494799  295729  344879   
59  20230103  58KDB  Province Nord  POUEMBOUT  12.518028  295572  345328   

   cuirasse  cuira_area bdtopo  bdtop_area lay

c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning:

les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont identiques.          date    nom      province     commune    surface       x       y  \
105  20230103  58KEA  Province Sud  BOULOUPARI   9.573837  393195  259016   
110  20230103  58KEA  Province Sud  BOULOUPARI  14.815930  393123  259483   

    cuirasse  cuira_area bdtopo  bdtop_area layer  path  \
105     None         NaN   None         NaN  None  None   
110     None         NaN   None         NaN  None  None   

                                              geometry   ID  groupe_id  
105  MULTIPOLYGON (((393298.100 259345.700, 393298....  106       31.0  
110  MULTIPOLYGON (((393245.100 259805.400, 393245....  111       31.0  
les noms des tuiles sont identiques.          date    nom      province     commune   surface       x       y  \
127  20230103  58KEA  Province Sud  BOULOUPARI  4.771889  395878  255325   
1

c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning:

...

c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning:

les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont identiques.            date    nom      province    commune    surface       x       y  \
22280  20231129  58KFA  Province Sud  MONT DORE   5.730504  459734  221111   
22281  20231129  58KFA  Province Sud  MONT DORE  14.031167  460223  221332   
22283  20231129  58KFA  Province Sud  MONT DORE   2.810240  459979  221314   
22291  20231129  58KFA  Province Sud  M

c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning:

les noms des tuiles sont identiques.            date    nom           province commune   surface       x       y  \
22402  20231221  58KGB  Province des Iles   LIFOU  2.287929  545897  343112   
22403  20231221  58KGB  Province des Iles   LIFOU  1.988199  545979  343294   

      cuirasse  cuira_area bdtopo  bdtop_area layer  path  \
22402     None         NaN   None         NaN  None  None   
22403     None         NaN   None         NaN  None  None   

                                                geometry     ID  groupe_id  
22402  MULTIPOLYGON (((545843.100 343210.900, 545843....  22403     2745.0  
22403  MULTIPOLYGON (((545881.800 343411.100, 545882....  22404     2745.0  
les noms des tuiles sont identiques.            date    nom      province       commune   surface       x       y  \
22422  20231221  58KGA  Province Sud  ILE DES PINS  3.867583  549216  179526   
22426  20231221  58KGA  Province Sud  ILE DES PINS  1.109311  548931  179516   

      cuirasse  cuira_area bdtop

c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning:

In [24]:
surfdetect_control=surfdetect_control.reset_index(drop=True)
surfdetect_control['ID'] = range(1, len(surfdetect_control)+1,1)

In [ ]:
# Check if the geometry is a Polygon 
for i in range(len(surfdetect_control)):
    if surfdetect_control['geometry'].geom_type[i] == 'Polygon':
        surfdetect_control.at[i, 'geometry'] = MultiPolygon([surfdetect_control['geometry'][i]])
        #print(surfdetect_control)
    else:
        print("La géométrie n'est pas de type Polygon.")

In [ ]:
surfdetect_control['surface'] = surfdetect_control['geometry'].area/10000

In [ ]:
surfdetect_control=surfdetect_control.drop(columns={'groupe_id','ID','path','layer'})

## FINALISATION : Intégration des données dans la table "sentinel_surfaces_detectees"

In [ ]:
from sqlalchemy import text

def IntegrationSurfacesSentinelGPK(s, inf, project_db_schema,data, name_regr, conn, filter_date, chmps_s, chmps_orig):
    data.to_postgis(name_regr,conn, schema=project_db_schema,if_exists='replace')
    sqlintegr = text(f"INSERT INTO {project_db_schema}.{s} ({chmps_s}) " + \
        f"SELECT {chmps_orig} FROM {project_db_schema}.{name_regr}")
    print(sqlintegr)
    conn.connect().execute(sqlintegr)
    #insertion via table informations sentinel des nouveux identifiants
    sql_upd_info = text(f"INSERT INTO {project_db_schema}.{inf} (ogc_fid_surface, date_) " + \
        f"SELECT ogc_fid, date_ from {project_db_schema}.{s} where date_ >= '{filter_date}'")
    print(sql_upd_info)
    conn.connect().execute(sql_upd_info)

In [ ]:
s = "sentinel_surfaces_detectees"
inf = "sentinel_informations_surfaces_detectees_old"
datetxtdb = "date_texte"
datedb = "date_"
dateorig = "date"
chps = "nom, province, commune, surface, x, y, cuirasse, cuira_area, bdtopo, bdtop_area, geometry"
champs_s = f'{datetxtdb}, {chps}, {datedb}'
format_date_to_timestamp = 'YYYYMMDD'
champs_s_orig = f"{dateorig}, {chps}, to_timestamp({dateorig}, '{format_date_to_timestamp}')"
filt_date = '2023-01-01 00:00:00'
name_couche_temp="sentinel_surfaces_detectees_2023"

In [ ]:
conex = create_engine(f'postgresql://{os.getenv("DB_USER")}:{os.getenv("DB_PWD")}@{os.getenv("DB_HOST")}:{os.getenv("DB_PORT")}/{os.getenv("DB_WORKSPACE")}')
IntegrationSurfacesSentinelGPK(s, inf, os.getenv("DB_SCHEMA"),surfdetect_control , name_couche_temp, conex, filt_date, champs_s, champs_s_orig)
conex.dispose()
del conex